In [ ]:
# Import the necessary libraries
import numpy as np
import pandas as pd
import hvplot.pandas
from pathlib import Path

import warnings
warnings.filterwarnings('ignore')

pd.set_option('display.max_rows', None)  # To show all rows
pd.set_option('display.max_columns', None)  # To show all columns

In [2]:
# Read in the CSV files that contain SMA, EMA, and BB/RSI inidcators based on ratio data
googl_df = pd.read_csv("Resources/googl_ratio_indicators.csv", infer_datetime_format=True, index_col="Date", parse_dates=True)
nvda_df = pd.read_csv("Resources/nvda_ratio_indicators.csv", infer_datetime_format=True, index_col="Date", parse_dates=True)
mmm_df = pd.read_csv("Resources/mmm_ratio_indicators.csv", infer_datetime_format=True, index_col="Date", parse_dates=True)
pg_df = pd.read_csv("Resources/pg_ratio_indicators.csv", infer_datetime_format=True, index_col="Date", parse_dates=True)

In [3]:
# Create a list of tuples containing the stock DataFrames and their respective columns for iteration
ticker_data_all = [
    (googl_df, [("GOOGL P/S (LTM)", "ps"), ("GOOGL P/FCF (LTM)", "pfcf"), ("GOOGL P/E (LTM)", "pe")]),
    (nvda_df, [("NVDA P/S (LTM)", "ps"), ("NVDA P/FCF (LTM)", "pfcf"), ("NVDA P/E (LTM)", "pe")]),
    (mmm_df, [("MMM P/S (LTM)", "ps"), ("MMM P/FCF (LTM)", "pfcf"), ("MMM P/E (LTM)", "pe")]),
    (pg_df, [("PG P/S (LTM)", "ps"), ("PG P/FCF (LTM)", "pfcf"), ("PG P/E (LTM)", "pe")]),
]

# Create and Populate the "signal" column for signal DataFrames
for df, metrics in ticker_data_all:
    for column_name, prefix, in metrics:
        df[f'{prefix}_Signal_sma'] = 0.0
        df[f'{prefix}_Signal_ema'] = 0.0
        df[f'{prefix}_Signal_bb_rsi'] = 0.0

In [4]:
# Generate the trading signal 0 or 1,
# where 1 is when sma_fast is greater than sma_slow or ema_fast is greater than ema_slow
# and 0 otherwise
for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        # Apply the condition to set the 'Signal' column
        df[f'{prefix}_Signal_sma'] = np.where(df[f'{prefix}_sma_fast'] > df[f'{prefix}_sma_slow'], 1.0, 0.0)
        df[f'{prefix}_Signal_ema'] = np.where(df[f'{prefix}_ema_fast'] > df[f'{prefix}_ema_slow'], 1.0, 0.0)

In [5]:
# Calculate the points in time when the Signal value changes
# Identify trade entry (1) and exit (-1) points
for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        df[f'{prefix}_Entry/Exit_sma'] = df[f'{prefix}_Signal_sma'].diff()
        df[f'{prefix}_Entry/Exit_ema'] = df[f'{prefix}_Signal_ema'].diff()

### Bollinger Band and RSI Trading Signals and Entry/Exit points

In [6]:
# # Generate the trading signals 0 or 1
# signals_googl_df['bb_rsi_buy'] = np.where((signals_googl_df['GOOGL Adj. Close'] < googl_df['bb_lower_talib']) & (googl_df['RSI'] < 30), 1, 0)
# signals_googl_df['bb_rsi_sell'] = np.where((signals_googl_df['GOOGL Adj. Close'] > googl_df['bb_upper_talib']) & (googl_df['RSI'] > 70), 1, 0)

# signals_nvda_df['bb_rsi_buy'] = np.where((signals_nvda_df['NVDA Adj. Close'] < nvda_df['bb_lower_talib']) & (nvda_df['RSI'] < 30), 1, 0)
# signals_nvda_df['bb_rsi_sell'] = np.where((signals_nvda_df['NVDA Adj. Close'] > nvda_df['bb_upper_talib']) & (nvda_df['RSI'] > 70), 1, 0)

# signals_mmm_df['bb_rsi_buy'] = np.where((signals_mmm_df['MMM Adj. Close'] < mmm_df['bb_lower_talib']) & (mmm_df['RSI'] < 30), 1, 0)
# signals_mmm_df['bb_rsi_sell'] = np.where((signals_mmm_df['MMM Adj. Close'] > mmm_df['bb_upper_talib']) & (mmm_df['RSI'] > 70), 1, 0)

# signals_pg_df['bb_rsi_buy'] = np.where((signals_pg_df['PG Adj. Close'] < pg_df['bb_lower_talib']) & (pg_df['RSI'] < 30), 1, 0)
# signals_pg_df['bb_rsi_sell'] = np.where((signals_pg_df['PG Adj. Close'] > pg_df['bb_upper_talib']) & (pg_df['RSI'] > 70), 1, 0)

In [7]:
# # Convert sell signals to -1
# for df in signal_dfs:
#     df['bb_rsi_sell'] *= -1
#     # Combine bb buy and sell signals into 'Signal_bb_rsi' column
#     df['bb_rsi_combined'] = df['bb_rsi_buy'] + df['bb_rsi_sell']

In [8]:
# # Calculate the points in time when the Signal value changes
# # Identify trade entry (1) and exit (-1) points
# for signals_df, source_df in df_pairs:
#     signals_df['Signal_bb_rsi'] = signals_df['bb_rsi_combined'].diff()
#     #signals_df['Signal_bb_rsi'] = signals_df['Signal_bb_rsi'].fillna(0, inplace=True)
#     signals_df['Entry/Exit_bb_rsi'] = signals_df['Signal_bb_rsi']   

In [9]:
# # Drop unnecessary calculation columns
# for df in signal_dfs:
#     df.drop(columns=['bb_rsi_buy', 'bb_rsi_sell', 'bb_rsi_combined'], inplace=True)

### SMA Entry/Exit Plots

In [10]:
# Initialize a dictionary to store the plots for SMA strategy from each ratio for each stock
plots_sma = {}

for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        
        # Extract the stock symbol from the column names (assuming 'Adj. Close' is part of the name)
        stock_symbol = [col for col in df.columns if 'Adj. Close' in col][0].split()[0]
        
        # Plot exit positions
        exit = df[df[f'{prefix}_Entry/Exit_sma'] == -1.0][f'{stock_symbol} Adj. Close'].hvplot.scatter(
            color='orange',
            marker='v',
            size=200,
            legend=False,
            ylabel='Price in $',
            width=1000,
            height=400
        )

        # Plot entry positions
        entry = df[df[f'{prefix}_Entry/Exit_sma'] == 1.0][f'{stock_symbol} Adj. Close'].hvplot.scatter(
            color='purple',
            marker='^',
            size=200,
            legend=False,
            ylabel='Price in $',
            width=1000,
            height=400
        )

        # Plot security close price
        security_close = df[[f'{stock_symbol} Adj. Close']].hvplot(
            line_color='lightgray',
            ylabel='Price in $',
            width=1000,
            height=400
        )

        # Plot moving averages
        moving_avgs = df[[f'{prefix}_sma_fast', f'{prefix}_sma_slow']].hvplot(
            ylabel='Price in $',
            width=1000,
            height=400
        )

        # Create the overlay plot
        entry_exit_plot = security_close * moving_avgs * entry * exit

        # Set the title dynamically based on the stock symbol
        entry_exit_plot = entry_exit_plot.opts(
            title=f"{stock_symbol} - SMA10, SMA100, Entry and Exit Points - from {prefix.upper()} Ratio"
        )

        # Store the plot in the dictionary using the stock symbol and ratio prefix as key
        
        plots_sma[f"{stock_symbol}_{prefix}"] = entry_exit_plot

### EMA Entry/Exit Plots

In [11]:
# Initialize a dictionary to store the plots for SMA strategy from each ratio for each stock
plots_ema = {}

for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        
        # Extract the stock symbol from the column names (assuming 'Adj. Close' is part of the name)
        stock_symbol = [col for col in df.columns if 'Adj. Close' in col][0].split()[0]
        
        # Plot exit positions
        exit = df[df[f'{prefix}_Entry/Exit_ema'] == -1.0][f'{stock_symbol} Adj. Close'].hvplot.scatter(
            color='orange',
            marker='v',
            size=200,
            legend=False,
            ylabel='Price in $',
            width=1000,
            height=400
        )

        # Plot entry positions
        entry = df[df[f'{prefix}_Entry/Exit_ema'] == 1.0][f'{stock_symbol} Adj. Close'].hvplot.scatter(
            color='purple',
            marker='^',
            size=200,
            legend=False,
            ylabel='Price in $',
            width=1000,
            height=400
        )

        # Plot security close price
        security_close = df[[f'{stock_symbol} Adj. Close']].hvplot(
            line_color='lightgray',
            ylabel='Price in $',
            width=1000,
            height=400
        )

        # Plot moving averages
        moving_avgs = df[[f'{prefix}_ema_fast', f'{prefix}_ema_slow']].hvplot(
            ylabel='Price in $',
            width=1000,
            height=400
        )

        # Create the overlay plot
        entry_exit_plot = security_close * moving_avgs * entry * exit

        # Set the title dynamically based on the stock symbol
        entry_exit_plot = entry_exit_plot.opts(
            title=f"{stock_symbol} - EMA10, EMA100, Entry and Exit Points - from {prefix.upper()} Ratio"
        )

        # Store the plot in the dictionary using the stock symbol and ratio prefix as key
        
        plots_ema[f"{stock_symbol}_{prefix}"] = entry_exit_plot

### BB and RSI Entry/Exit Plots

In [12]:
# # Initialize a dictionary to store the plots for BB & RSI strategy for each stock
# plots_bb_rsi = {}

# for signals_df, source_df in df_pairs:
#     # Extract the stock symbol from the column names (assuming 'Adj. Close' is part of the name)
#     stock_symbol = [col for col in signals_df.columns if 'Adj. Close' in col][0].split()[0]

#     # Plot exit positions
#     exit = signals_df[signals_df['Entry/Exit_bb_rsi'] == -1.0][f'{stock_symbol} Adj. Close'].hvplot.scatter(
#         color='orange',
#         marker='v',
#         size=200,
#         legend=False,
#         ylabel='Price in $',
#         width=1000,
#         height=400
#     )

#     # Plot entry positions
#     entry = signals_df[signals_df['Entry/Exit_bb_rsi'] == 1.0][f'{stock_symbol} Adj. Close'].hvplot.scatter(
#         color='purple',
#         marker='^',
#         size=200,
#         legend=False,
#         ylabel='Price in $',
#         width=1000,
#         height=400
#     )

#     # Plot security close price
#     security_close = signals_df[[f'{stock_symbol} Adj. Close']].hvplot(
#         line_color='lightgray',
#         ylabel='Price in $',
#         width=1000,
#         height=400
#     )

#     # Plot moving averages
#     moving_avgs = source_df[['bb_upper_talib', 'bb_mid_talib', 'bb_lower_talib', 'RSI']].hvplot(
#         ylabel='Price in $',
#         width=1000,
#         height=400
#     )

#     # Create the overlay plot
#     entry_exit_plot = security_close * moving_avgs * entry * exit

#     # Set the title dynamically based on the stock symbol
#     entry_exit_plot = entry_exit_plot.opts(
#         title=f"{stock_symbol} - Bollinger Bands & RSI, Entry and Exit Points"
#     )

#     # Store the plot in the dictionary using the stock symbol as key
#     plots_bb_rsi[stock_symbol] = entry_exit_plot

### Investment Capital Tracking

In [13]:
# Set initial investment capital
initial_capital = float(100000)

# Set the share size per transaction
share_size = 500

In [14]:
# Creating a position column to store the number of shares held
# Buy a 500 share position when the dual moving average crossover Signal equals 1
# Otherwise, `Position` should be zero (sell)

for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        df[f'{prefix}_Position_sma'] = share_size * df[f'{prefix}_Signal_sma']
        df[f'{prefix}_Position_ema'] = share_size * df[f'{prefix}_Signal_ema']
        #df['Position_bb_rsi'] = share_size * df['Signal_bb_rsi']

In [15]:
# Determine the points in time where the share position is bought or sold
for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        df[f'{prefix}_Entry/Exit Position_sma'] = df[f'{prefix}_Position_sma'].diff()
        df[f'{prefix}_Entry/Exit Position_ema'] = df[f'{prefix}_Position_ema'].diff()
        #df[f'{prefix}_Entry/Exit Position_bb_rsi'] = df[f'{prefix}_Position_bb_rsi'].diff()

In [16]:
# Multiply the close price by the number of shares held, or the Position
for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        adj_close_col = [col for col in df.columns if 'Adj. Close' in col][0].split()[0]
        df[f'{prefix}_Portfolio Holdings_sma'] = df[f'{adj_close_col} Adj. Close'] * df[f'{prefix}_Position_sma']
        df[f'{prefix}_Portfolio Holdings_ema'] = df[f'{adj_close_col} Adj. Close'] * df[f'{prefix}_Position_ema']
        #df[f'{prefix}_Portfolio Holdings_bb_rsi'] = df[adj_close_col] * df[f'{prefix}_Position_bb_rsi']

In [17]:
# Subtract the amount of either the cost or proceeds of the trade from the initial capital invested
for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        adj_close_col = [col for col in df.columns if 'Adj. Close' in col][0].split()[0]
        df[f'{prefix}_Portfolio Cash_sma'] = initial_capital - (df[f'{adj_close_col} Adj. Close'] * df[f'{prefix}_Entry/Exit Position_sma']).cumsum()
        df[f'{prefix}_Portfolio Cash_ema'] = initial_capital - (df[f'{adj_close_col} Adj. Close'] * df[f'{prefix}_Entry/Exit Position_ema']).cumsum()
        #df['Portfolio Cash_bb_rsi'] = initial_capital - (df[adj_close_col] * df['Entry/Exit Position_bb_rsi']).cumsum()

In [18]:
# Calculate the total portfolio value by adding the portfolio cash to the portfolio holdings (or investments)
for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        df[f'{prefix}_Portfolio Total_sma'] = df[f'{prefix}_Portfolio Cash_sma'] + df[f'{prefix}_Portfolio Holdings_sma']
        df[f'{prefix}_Portfolio Total_ema'] = df[f'{prefix}_Portfolio Cash_ema'] + df[f'{prefix}_Portfolio Holdings_ema']
        #df['Portfolio Total_bb_rsi'] = df['Portfolio Cash_bb_rsi'] + df['Portfolio Holdings_bb_rsi']

In [19]:
# Calculate the portfolio daily returns
for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        df[f'{prefix}_Portfolio Daily Returns_sma'] = df[f'{prefix}_Portfolio Total_sma'].pct_change()
        df[f'{prefix}_Portfolio Daily Returns_ema'] = df[f'{prefix}_Portfolio Total_ema'].pct_change()
        #df['Portfolio Daily Returns_bb_rsi'] = df['Portfolio Total_bb_rsi'].pct_change()

In [20]:
# Calculate the portfolio cumulative returns
for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        df[f'{prefix}_Portfolio Cumulative Returns_sma'] = (1 + df[f'{prefix}_Portfolio Daily Returns_sma']).cumprod() - 1
        df[f'{prefix}_Portfolio Cumulative Returns_ema'] = (1 + df[f'{prefix}_Portfolio Daily Returns_ema']).cumprod() - 1
        # df['Portfolio Cumulative Returns_bb_rsi'] = (1 + df['Portfolio Daily Returns_bb_rsi']).cumprod() - 1

### SMA Portfolio Value Plots for each ticker

In [21]:
# Initialize a dictionary to store the plots
plots_sma_portfolio_value = {}

for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        
        # Extract the stock symbol from the column names (assuming 'Adj. Close' is part of the name)
        stock_symbol = [col for col in df.columns if 'Adj. Close' in col][0].split()[0]
        
        # Visualize exit position relative to total portfolio value
        exit = df[df[f'{prefix}_Entry/Exit_sma'] == -1.0][f'{prefix}_Portfolio Total_sma'].hvplot.scatter(
            color='orange',
            marker='v',
            size=200,
            legend=False,
            ylabel='Total Portfolio Value',
            width=1000,
            height=400
        )

        # Visualize entry position relative to total portfolio value
        entry = df[df[f'{prefix}_Entry/Exit_sma'] == 1.0][f'{prefix}_Portfolio Total_sma'].hvplot.scatter(
            color='purple',
            marker='^',
            size=200,
            ylabel='Total Portfolio Value',
            width=1000,
            height=400
        )

        # Visualize the value of the total portfolio
        total_portfolio_value = df[[f'{prefix}_Portfolio Total_sma']].hvplot(
            line_color='lightgray',
            ylabel='Total Portfolio Value',
            xlabel='Date',
            width=1000,
            height=400
        )

        # Overlay the plots
        portfolio_entry_exit_plot = total_portfolio_value * entry * exit

        # Set the title dynamically based on the stock symbol
        portfolio_entry_exit_plot = portfolio_entry_exit_plot.opts(
            title=f"{stock_symbol} - SMA10, SMA100, Total Portfolio Value - from {prefix.upper()} Ratio",
            yformatter='%.0f'
        )

        # Store the plot in the dictionary using the stock symbol as key
        plots_sma_portfolio_value[f"{stock_symbol}_{prefix}"] = portfolio_entry_exit_plot

### EMA Portfolio Value Plots for each ticker

In [22]:
# Initialize a dictionary to store the plots
plots_ema_portfolio_value = {}

for df, metrics in ticker_data_all:
    for column_name, prefix in metrics:
        
        # Extract the stock symbol from the column names (assuming 'Adj. Close' is part of the name)
        stock_symbol = [col for col in df.columns if 'Adj. Close' in col][0].split()[0]
        
        # Visualize exit position relative to total portfolio value
        exit = df[df[f'{prefix}_Entry/Exit_ema'] == -1.0][f'{prefix}_Portfolio Total_ema'].hvplot.scatter(
            color='orange',
            marker='v',
            size=200,
            legend=False,
            ylabel='Total Portfolio Value',
            width=1000,
            height=400
        )

        # Visualize entry position relative to total portfolio value
        entry = df[df[f'{prefix}_Entry/Exit_ema'] == 1.0][f'{prefix}_Portfolio Total_ema'].hvplot.scatter(
            color='purple',
            marker='^',
            size=200,
            ylabel='Total Portfolio Value',
            width=1000,
            height=400
        )

        # Visualize the value of the total portfolio
        total_portfolio_value = df[[f'{prefix}_Portfolio Total_ema']].hvplot(
            line_color='lightgray',
            ylabel='Total Portfolio Value',
            xlabel='Date',
            width=1000,
            height=400
        )

        # Overlay the plots
        portfolio_entry_exit_plot = total_portfolio_value * entry * exit

        # Set the title dynamically based on the stock symbol
        portfolio_entry_exit_plot = portfolio_entry_exit_plot.opts(
            title=f"{stock_symbol} - EMA10, EMA100, Total Portfolio Value - from {prefix.upper()} Ratio",
            yformatter='%.0f'
        )

        # Store the plot in the dictionary using the stock symbol as key
        plots_ema_portfolio_value[f"{stock_symbol}_{prefix}"] = portfolio_entry_exit_plot

### BB & RSI Portfolio Value Plots for each ticker

In [23]:
# # Initialize a dictionary to store the plots
# plots_bb_rsi_portfolio_value = {}

# for df in signal_dfs:
    
#     # Extract the stock symbol from the column names (assuming 'Adj. Close' is part of the name)
#     stock_symbol = [col for col in df.columns if 'Adj. Close' in col][0].split()[0]

#     # Visualize exit position relative to total portfolio value
#     exit = df[df['Entry/Exit_bb_rsi'] == -1.0]['Portfolio Total_bb_rsi'].hvplot.scatter(
#         color='orange',
#         marker='v',
#         size=200,
#         legend=False,
#         ylabel='Total Portfolio Value',
#         width=1000,
#         height=400
#     )

#     # Visualize entry position relative to total portfolio value
#     entry = df[df['Entry/Exit_bb_rsi'] == 1.0]['Portfolio Total_bb_rsi'].hvplot.scatter(
#         color='purple',
#         marker='^',
#         size=200,
#         ylabel='Total Portfolio Value',
#         width=1000,
#         height=400
#     )

#     # Visualize the value of the total portfolio
#     total_portfolio_value = df[['Portfolio Total_bb_rsi']].hvplot(
#         line_color='lightgray',
#         ylabel='Total Portfolio Value',
#         xlabel='Date',
#         width=1000,
#         height=400
#     )

#     # Overlay the plots
#     portfolio_entry_exit_plot = total_portfolio_value * entry * exit

#     # Set the title dynamically based on the stock symbol
#     portfolio_entry_exit_plot = portfolio_entry_exit_plot.opts(
#         title=f"{stock_symbol} - Bollinger Bands & RSI Total Portfolio Value",
#         yformatter='%.0f'
#     )

#     # Store the plot in the dictionary using the stock symbol as key
#     plots_bb_rsi_portfolio_value[stock_symbol] = portfolio_entry_exit_plot

### Save all stock DataFrames as CSVs for training models

In [24]:
# Write individual stock DFs w/ SMA, EMA, and BB/RSI to CSV
googl_df.to_csv('Resources/googl_signals.csv', index=True)
nvda_df.to_csv('Resources/nvda_signals.csv', index=True)
mmm_df.to_csv('Resources/mmm_signals.csv', index=True)
pg_df.to_csv('Resources/pg_signals.csv', index=True)

### Display All Plots

In [25]:
# Plot the SMA (from each ratio) entry and exit points for each stock
# NOTE: This will display 12 plots (3 per stock)
for plot in plots_sma.values():
    display(plot)


:Overlay
   .Curve.I                              :Curve   [Date]   (GOOGL Adj. Close)
   .NdOverlay.I                          :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.GOOGL_Adj_full_stop_Close.I  :Scatter   [Date]   (GOOGL Adj. Close)
   .Scatter.GOOGL_Adj_full_stop_Close.II :Scatter   [Date]   (GOOGL Adj. Close)

:Overlay
   .Curve.I                              :Curve   [Date]   (GOOGL Adj. Close)
   .NdOverlay.I                          :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.GOOGL_Adj_full_stop_Close.I  :Scatter   [Date]   (GOOGL Adj. Close)
   .Scatter.GOOGL_Adj_full_stop_Close.II :Scatter   [Date]   (GOOGL Adj. Close)

:Overlay
   .Curve.I                              :Curve   [Date]   (GOOGL Adj. Close)
   .NdOverlay.I                          :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.GOOGL_Adj_full_stop_Close.I  :Scatter   [Date]   (GOOGL Adj. Close)
   .Scatter.GOOGL_Adj_full_stop_Close.II :Scatter   [Date]   (GOOGL Adj. Close)

:Overlay
   .Curve.I                             :Curve   [Date]   (NVDA Adj. Close)
   .NdOverlay.I                         :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.NVDA_Adj_full_stop_Close.I  :Scatter   [Date]   (NVDA Adj. Close)
   .Scatter.NVDA_Adj_full_stop_Close.II :Scatter   [Date]   (NVDA Adj. Close)

:Overlay
   .Curve.I                             :Curve   [Date]   (NVDA Adj. Close)
   .NdOverlay.I                         :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.NVDA_Adj_full_stop_Close.I  :Scatter   [Date]   (NVDA Adj. Close)
   .Scatter.NVDA_Adj_full_stop_Close.II :Scatter   [Date]   (NVDA Adj. Close)

...

:Overlay
   .Curve.I                            :Curve   [Date]   (MMM Adj. Close)
   .NdOverlay.I                        :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.MMM_Adj_full_stop_Close.I  :Scatter   [Date]   (MMM Adj. Close)
   .Scatter.MMM_Adj_full_stop_Close.II :Scatter   [Date]   (MMM Adj. Close)

:Overlay
   .Curve.I                            :Curve   [Date]   (MMM Adj. Close)
   .NdOverlay.I                        :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.MMM_Adj_full_stop_Close.I  :Scatter   [Date]   (MMM Adj. Close)
   .Scatter.MMM_Adj_full_stop_Close.II :Scatter   [Date]   (MMM Adj. Close)

:Overlay
   .Curve.I                           :Curve   [Date]   (PG Adj. Close)
   .NdOverlay.I                       :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.PG_Adj_full_stop_Close.I  :Scatter   [Date]   (PG Adj. Close)
   .Scatter.PG_Adj_full_stop_Close.II :Scatter   [Date]   (PG Adj. Close)

:Overlay
   .Curve.I                           :Curve   [Date]   (PG Adj. Close)
   .NdOverlay.I                       :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.PG_Adj_full_stop_Close.I  :Scatter   [Date]   (PG Adj. Close)
   .Scatter.PG_Adj_full_stop_Close.II :Scatter   [Date]   (PG Adj. Close)

:Overlay
   .Curve.I                           :Curve   [Date]   (PG Adj. Close)
   .NdOverlay.I                       :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.PG_Adj_full_stop_Close.I  :Scatter   [Date]   (PG Adj. Close)
   .Scatter.PG_Adj_full_stop_Close.II :Scatter   [Date]   (PG Adj. Close)

In [26]:
# Plot the EMA (from each ratio) entry and exit points for each stock
# NOTE: This will display 12 plots (3 per stock)
for plot in plots_ema.values():
    display(plot)

:Overlay
   .Curve.I                              :Curve   [Date]   (GOOGL Adj. Close)
   .NdOverlay.I                          :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.GOOGL_Adj_full_stop_Close.I  :Scatter   [Date]   (GOOGL Adj. Close)
   .Scatter.GOOGL_Adj_full_stop_Close.II :Scatter   [Date]   (GOOGL Adj. Close)

:Overlay
   .Curve.I                              :Curve   [Date]   (GOOGL Adj. Close)
   .NdOverlay.I                          :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.GOOGL_Adj_full_stop_Close.I  :Scatter   [Date]   (GOOGL Adj. Close)
   .Scatter.GOOGL_Adj_full_stop_Close.II :Scatter   [Date]   (GOOGL Adj. Close)

:Overlay
   .Curve.I                              :Curve   [Date]   (GOOGL Adj. Close)
   .NdOverlay.I                          :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.GOOGL_Adj_full_stop_Close.I  :Scatter   [Date]   (GOOGL Adj. Close)
   .Scatter.GOOGL_Adj_full_stop_Close.II :Scatter   [Date]   (GOOGL Adj. Close)

:Overlay
   .Curve.I                             :Curve   [Date]   (NVDA Adj. Close)
   .NdOverlay.I                         :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.NVDA_Adj_full_stop_Close.I  :Scatter   [Date]   (NVDA Adj. Close)
   .Scatter.NVDA_Adj_full_stop_Close.II :Scatter   [Date]   (NVDA Adj. Close)

:Overlay
   .Curve.I                             :Curve   [Date]   (NVDA Adj. Close)
   .NdOverlay.I                         :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.NVDA_Adj_full_stop_Close.I  :Scatter   [Date]   (NVDA Adj. Close)
   .Scatter.NVDA_Adj_full_stop_Close.II :Scatter   [Date]   (NVDA Adj. Close)

...

:Overlay
   .Curve.I                            :Curve   [Date]   (MMM Adj. Close)
   .NdOverlay.I                        :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.MMM_Adj_full_stop_Close.I  :Scatter   [Date]   (MMM Adj. Close)
   .Scatter.MMM_Adj_full_stop_Close.II :Scatter   [Date]   (MMM Adj. Close)

:Overlay
   .Curve.I                            :Curve   [Date]   (MMM Adj. Close)
   .NdOverlay.I                        :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.MMM_Adj_full_stop_Close.I  :Scatter   [Date]   (MMM Adj. Close)
   .Scatter.MMM_Adj_full_stop_Close.II :Scatter   [Date]   (MMM Adj. Close)

:Overlay
   .Curve.I                           :Curve   [Date]   (PG Adj. Close)
   .NdOverlay.I                       :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.PG_Adj_full_stop_Close.I  :Scatter   [Date]   (PG Adj. Close)
   .Scatter.PG_Adj_full_stop_Close.II :Scatter   [Date]   (PG Adj. Close)

:Overlay
   .Curve.I                           :Curve   [Date]   (PG Adj. Close)
   .NdOverlay.I                       :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.PG_Adj_full_stop_Close.I  :Scatter   [Date]   (PG Adj. Close)
   .Scatter.PG_Adj_full_stop_Close.II :Scatter   [Date]   (PG Adj. Close)

:Overlay
   .Curve.I                           :Curve   [Date]   (PG Adj. Close)
   .NdOverlay.I                       :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.PG_Adj_full_stop_Close.I  :Scatter   [Date]   (PG Adj. Close)
   .Scatter.PG_Adj_full_stop_Close.II :Scatter   [Date]   (PG Adj. Close)

In [27]:
# Plot the SMA (from each ratio) Total Portfolio Value for each stock
# NOTE: This will display 12 plots (3 per stock)
for plot in plots_sma_portfolio_value.values():
    display(plot)

:Overlay
   .Curve.I                           :Curve   [Date]   (ps_Portfolio Total_sma)
   .Scatter.Ps_Portfolio_Total_sma.I  :Scatter   [Date]   (ps_Portfolio Total_sma)
   .Scatter.Ps_Portfolio_Total_sma.II :Scatter   [Date]   (ps_Portfolio Total_sma)

:Overlay
   .Curve.I                             :Curve   [Date]   (pfcf_Portfolio Total_sma)
   .Scatter.Pfcf_Portfolio_Total_sma.I  :Scatter   [Date]   (pfcf_Portfolio Total_sma)
   .Scatter.Pfcf_Portfolio_Total_sma.II :Scatter   [Date]   (pfcf_Portfolio Total_sma)

:Overlay
   .Curve.I                           :Curve   [Date]   (pe_Portfolio Total_sma)
   .Scatter.Pe_Portfolio_Total_sma.I  :Scatter   [Date]   (pe_Portfolio Total_sma)
   .Scatter.Pe_Portfolio_Total_sma.II :Scatter   [Date]   (pe_Portfolio Total_sma)

:Overlay
   .Curve.I                           :Curve   [Date]   (ps_Portfolio Total_sma)
   .Scatter.Ps_Portfolio_Total_sma.I  :Scatter   [Date]   (ps_Portfolio Total_sma)
   .Scatter.Ps_Portfolio_Total_sma.II :Scatter   [Date]   (ps_Portfolio Total_sma)

:Overlay
   .Curve.I                             :Curve   [Date]   (pfcf_Portfolio Total_sma)
   .Scatter.Pfcf_Portfolio_Total_sma.I  :Scatter   [Date]   (pfcf_Portfolio Total_sma)
   .Scatter.Pfcf_Portfolio_Total_sma.II :Scatter   [Date]   (pfcf_Portfolio Total_sma)

...

:Overlay
   .Curve.I                             :Curve   [Date]   (pfcf_Portfolio Total_sma)
   .Scatter.Pfcf_Portfolio_Total_sma.I  :Scatter   [Date]   (pfcf_Portfolio Total_sma)
   .Scatter.Pfcf_Portfolio_Total_sma.II :Scatter   [Date]   (pfcf_Portfolio Total_sma)

:Overlay
   .Curve.I                           :Curve   [Date]   (pe_Portfolio Total_sma)
   .Scatter.Pe_Portfolio_Total_sma.I  :Scatter   [Date]   (pe_Portfolio Total_sma)
   .Scatter.Pe_Portfolio_Total_sma.II :Scatter   [Date]   (pe_Portfolio Total_sma)

:Overlay
   .Curve.I                           :Curve   [Date]   (ps_Portfolio Total_sma)
   .Scatter.Ps_Portfolio_Total_sma.I  :Scatter   [Date]   (ps_Portfolio Total_sma)
   .Scatter.Ps_Portfolio_Total_sma.II :Scatter   [Date]   (ps_Portfolio Total_sma)

:Overlay
   .Curve.I                             :Curve   [Date]   (pfcf_Portfolio Total_sma)
   .Scatter.Pfcf_Portfolio_Total_sma.I  :Scatter   [Date]   (pfcf_Portfolio Total_sma)
   .Scatter.Pfcf_Portfolio_Total_sma.II :Scatter   [Date]   (pfcf_Portfolio Total_sma)

:Overlay
   .Curve.I                           :Curve   [Date]   (pe_Portfolio Total_sma)
   .Scatter.Pe_Portfolio_Total_sma.I  :Scatter   [Date]   (pe_Portfolio Total_sma)
   .Scatter.Pe_Portfolio_Total_sma.II :Scatter   [Date]   (pe_Portfolio Total_sma)

In [28]:
# Plot the EMA (from each ratio) Total Portfolio Value for each stock
# NOTE: This will display 12 plots (3 per stock)
for plot in plots_ema_portfolio_value.values():
    display(plot)

:Overlay
   .Curve.I                           :Curve   [Date]   (ps_Portfolio Total_ema)
   .Scatter.Ps_Portfolio_Total_ema.I  :Scatter   [Date]   (ps_Portfolio Total_ema)
   .Scatter.Ps_Portfolio_Total_ema.II :Scatter   [Date]   (ps_Portfolio Total_ema)

:Overlay
   .Curve.I                             :Curve   [Date]   (pfcf_Portfolio Total_ema)
   .Scatter.Pfcf_Portfolio_Total_ema.I  :Scatter   [Date]   (pfcf_Portfolio Total_ema)
   .Scatter.Pfcf_Portfolio_Total_ema.II :Scatter   [Date]   (pfcf_Portfolio Total_ema)

:Overlay
   .Curve.I                           :Curve   [Date]   (pe_Portfolio Total_ema)
   .Scatter.Pe_Portfolio_Total_ema.I  :Scatter   [Date]   (pe_Portfolio Total_ema)
   .Scatter.Pe_Portfolio_Total_ema.II :Scatter   [Date]   (pe_Portfolio Total_ema)

:Overlay
   .Curve.I                           :Curve   [Date]   (ps_Portfolio Total_ema)
   .Scatter.Ps_Portfolio_Total_ema.I  :Scatter   [Date]   (ps_Portfolio Total_ema)
   .Scatter.Ps_Portfolio_Total_ema.II :Scatter   [Date]   (ps_Portfolio Total_ema)

:Overlay
   .Curve.I                             :Curve   [Date]   (pfcf_Portfolio Total_ema)
   .Scatter.Pfcf_Portfolio_Total_ema.I  :Scatter   [Date]   (pfcf_Portfolio Total_ema)
   .Scatter.Pfcf_Portfolio_Total_ema.II :Scatter   [Date]   (pfcf_Portfolio Total_ema)

...

:Overlay
   .Curve.I                             :Curve   [Date]   (pfcf_Portfolio Total_ema)
   .Scatter.Pfcf_Portfolio_Total_ema.I  :Scatter   [Date]   (pfcf_Portfolio Total_ema)
   .Scatter.Pfcf_Portfolio_Total_ema.II :Scatter   [Date]   (pfcf_Portfolio Total_ema)

:Overlay
   .Curve.I                           :Curve   [Date]   (pe_Portfolio Total_ema)
   .Scatter.Pe_Portfolio_Total_ema.I  :Scatter   [Date]   (pe_Portfolio Total_ema)
   .Scatter.Pe_Portfolio_Total_ema.II :Scatter   [Date]   (pe_Portfolio Total_ema)

:Overlay
   .Curve.I                           :Curve   [Date]   (ps_Portfolio Total_ema)
   .Scatter.Ps_Portfolio_Total_ema.I  :Scatter   [Date]   (ps_Portfolio Total_ema)
   .Scatter.Ps_Portfolio_Total_ema.II :Scatter   [Date]   (ps_Portfolio Total_ema)

:Overlay
   .Curve.I                             :Curve   [Date]   (pfcf_Portfolio Total_ema)
   .Scatter.Pfcf_Portfolio_Total_ema.I  :Scatter   [Date]   (pfcf_Portfolio Total_ema)
   .Scatter.Pfcf_Portfolio_Total_ema.II :Scatter   [Date]   (pfcf_Portfolio Total_ema)

:Overlay
   .Curve.I                           :Curve   [Date]   (pe_Portfolio Total_ema)
   .Scatter.Pe_Portfolio_Total_ema.I  :Scatter   [Date]   (pe_Portfolio Total_ema)
   .Scatter.Pe_Portfolio_Total_ema.II :Scatter   [Date]   (pe_Portfolio Total_ema)